# Se utiliza birdnet lib para extraer Embeddings de los audios. Continúa donde iba

¿Qué cambia en este código?
- ✅ Verifica si el archivo CSV ya existe. Si existe, carga los archivos procesados y los almacena en processed_files.
- ✅ Si el código se detiene, al reiniciarlo solo procesará los audios faltantes. Antes de procesar un audio, revisa si ya está en processed_files.
- ✅ Guarda los datos en el CSV después de cada audio. Usa mode='a' (append) para agregar nuevas filas sin sobrescribir el archivo.
- ✅ Evita problemas de memoria

🔹 Nuevas mejoras en el código
- ✅ Cuenta cuántos audios se han procesado en esta ejecución. La variable processed_count se incrementa después de cada audio.
- ✅ Cada 500 audios muestra un mensaje en pantalla- if processed_count % 500 == 0: imprime el número de audios procesados hasta ese momento.
- ✅ Sigue siendo seguro para interrupciones


Después de guardar en CSV, limpia la lista all_data.
Con este enfoque, si el código se detiene en cualquier momento, puedes simplemente volver a ejecutarlo y continuará desde el último audio procesado. 🚀

El problema es que es algo lento... porque solo usa un hilo de CPU

In [1]:
import librosa
import pandas as pd
from pathlib import Path
import gc
import soundfile as sf
import numpy as np
import glob
from birdnetlib import Recording
from birdnetlib.analyzer import Analyzer
import os

# Get the current working directory
cwd = Path.cwd()
project_root = cwd.parents[1]


# Define una función para obtener los archivos .wav dinámicamente
def get_audio_files(base_path, folder_name, pattern="**/*.[Ww][Aa][Vv]"):
    return glob.glob(f"{str(base_path)}/{folder_name}/{pattern}", recursive=True)

# Define el path base
base_path = project_root / 'Output_files' / 'Extended_audios'

# Usa la función para cada dataset
# audios_chiffchaff = get_audio_files(base_path, "chiffchaff-fg")
# audios_littleowl = get_audio_files(base_path, "littleowl-fg")
# audios_pipit = get_audio_files(base_path, "pipit-fg")
# audios_rtbc = get_audio_files(base_path, "rtbc-begging")
# audios_littlepenguin = get_audio_files(base_path, "littlepenguin-display_call-exhale")
audios_greatTit = get_audio_files(base_path, "greatTit_song-files")

print("Files found:")
# print(f"Audios chiffchaff: {len(audios_chiffchaff)}")
# print(f"Audios littleowl: {len(audios_littleowl)}")
# print(f"Audios pipit: {len(audios_pipit)}")
# print(f"Audios rtbc: {len(audios_rtbc)}")
# print(f"Audios littlepenguin: {len(audios_littlepenguin)}")
print(f"Audios greatTit: {len(audios_greatTit)}")

# Print the first few file paths for verification
# print(audios_chiffchaff[:5])  # Verify the first few paths generated for chiffchaff
# print(audios_littleowl[:5])  # Verify the first few paths generated for littleowl
# print(audios_pipit[:5])  # Verify the first few paths generated for pipit
# print(audios_rtbc[:5])  # Verify the first few paths generated for rtbc
# print(audios_littlepenguin[:5])  # Verify the first few paths generated for littlepenguin
# print(audios_greatTit[:5])  # Verify the first few paths generated for greatTit


# Crear el directorio si no existe
output_dir = project_root / 'Output_files' / 'Embeddings_from_3sPadding'
output_dir.mkdir(parents=True, exist_ok=True)

# Define the CSV files for each dataset

# csv_chiffchaff = output_dir / 'chiffchaff_embeddings.csv'
# csv_littleowl = output_dir / 'littleowl_embeddings.csv'
# csv_pipit = output_dir / 'pipit_embeddings.csv'
# csv_rtbc = output_dir / 'rtbc_embeddings.csv'
# csv_littlepenguin = output_dir / 'littlepenguin_embeddings.csv'
csv_greatTit = output_dir / 'greatTit_embeddings.csv'


# Decide the audio files and CSV filename to work with.
audios = audios_greatTit
csv_filename = csv_greatTit

Files found:
Audios greatTit: 74048


In [ ]:
# Initialize the BirdNET model
analyzer = Analyzer()

# Check if the CSV file already exists to retrieve processed audio files
if os.path.exists(csv_filename):
    df_existing = pd.read_csv(csv_filename)
    processed_files = set(df_existing["file_name"])  # Already processed files
else:
    df_existing = pd.DataFrame()
    processed_files = set()

# List of audio file paths

all_data = []
processed_count = 0  # Counter for files processed in this execution

# Iterate through each file in the list of audio files
for audio_path in audios:
    try:
        # Extract the file name without the path
        file_name = os.path.basename(audio_path)

        # Skip if the file has already been processed
        if file_name in processed_files:
            # print(f"Skipping {file_name}, already processed.")
            continue

        # Load the recording into BirdNET
        recording = Recording(analyzer, audio_path)
        recording.extract_embeddings()

        # Process the extracted embeddings
        for emb in recording.embeddings:
            row = {
                "path": audio_path,  # Full path of the file
                "file_name": file_name,  # File name without the path
                "start_time": emb['start_time'],
                "end_time": emb['end_time']
            }
            # Add the 1024 embedding values
            for i, value in enumerate(emb["embeddings"]):
                row[f"dim_{i+1}"] = value

            all_data.append(row)

        # Save to the CSV file after processing each audio
        df_partial = pd.DataFrame(all_data)
        df_partial.to_csv(csv_filename, mode='a', header=not os.path.exists(csv_filename), index=False)
        
        # Clear the list to save memory
        all_data = []

        # Increment counter
        processed_count += 1

        # Display a message every 200 processed audios
        if processed_count % 200 == 0:
            print(f"{processed_count} audios processed so far.")

    except Exception as e:
        print(f"Error processing {audio_path}: {e}")

print(f"Embeddings saved to {csv_filename}")


Labels loaded.
load model True
Model loaded.
Labels loaded.
load_species_list_model
Meta model loaded.


INFO: Created TensorFlow Lite XNNPACK delegate for CPU.


Skipping 20221O78_20220420_040000_100851200.WAV, already processed.
Skipping 20221O78_20220420_040000_109139968.WAV, already processed.
Skipping 20221O78_20220420_040000_110464256.WAV, already processed.
Skipping 20221O78_20220420_040000_115165440.WAV, already processed.
Skipping 20221O78_20220420_040000_115416320.WAV, already processed.
Skipping 20221O78_20220420_040000_118009600.WAV, already processed.
Skipping 20221O78_20220420_040000_118323840.WAV, already processed.
Skipping 20221O78_20220420_040000_118567680.WAV, already processed.
Skipping 20221O78_20220420_040000_122934400.WAV, already processed.
Skipping 20221O78_20220420_040000_124718080.WAV, already processed.
Skipping 20221O78_20220420_040000_126990720.WAV, already processed.
Skipping 20221O78_20220420_040000_130523904.WAV, already processed.
Skipping 20221O78_20220420_040000_133199360.WAV, already processed.
Skipping 20221O78_20220420_040000_143301888.WAV, already processed.
Skipping 20221O78_20220420_040000_143529984.WAV,

In [2]:
import pandas as pd
import os

# Check if the CSV file already exists to retrieve processed audio files
if os.path.exists(csv_filename):
    df_embeddings = pd.read_csv(csv_filename)
    processed_files = set(df_embeddings["file_name"])  # Already processed files
else:
    df_embeddings = pd.DataFrame()
    processed_files = set()

num_processed_audios = df_embeddings["path"].nunique()  # Or the correct column name
print(f"{num_processed_audios} different audios were successfully processed.")

# Convert the original list of audios to a set
original_audios = set(audios)

# Get the list of processed audios from the DataFrame
processed_audios = set(df_embeddings["path"].unique())

# Identify the audios that were not processed
unprocessed_audios = original_audios - processed_audios

# Display results
print(f"Total audios in the original list: {len(original_audios)}")
print(f"Total audios processed: {len(processed_audios)}")
print(f"Total audios not processed: {len(unprocessed_audios)}")

# If you want to see which audios were not processed:
print("Unprocessed audios:")
print("\n".join(unprocessed_audios))


52521 different audios were successfully processed.
Total audios in the original list: 74048
Total audios processed: 52521
Total audios not processed: 21527
Unprocessed audios:
/teamspace/studios/this_studio/Output_files/Extended_audios/greatTit_song-files/train/vz32978/20211SW49_20210425_040000_92128960.WAV
/teamspace/studios/this_studio/Output_files/Extended_audios/greatTit_song-files/val/pf71395/20221O68_20220415_040000_148591744.WAV
/teamspace/studios/this_studio/Output_files/Extended_audios/greatTit_song-files/val/pf71915/20221C160B_20220405_050000_66688128.WAV
/teamspace/studios/this_studio/Output_files/Extended_audios/greatTit_song-files/val/ty69216/20221MP74_20220413_050000_76630016.WAV
/teamspace/studios/this_studio/Output_files/Extended_audios/greatTit_song-files/train/vz31866/20221W33_20220416_050000_25647360.WAV
/teamspace/studios/this_studio/Output_files/Extended_audios/greatTit_song-files/train/vz30994/20221MP96_20220423_050000_53614592.WAV
/teamspace/studios/this_studio/